In [1]:
import torch
import torch.nn as nn
import torch.optim as optim
from torchvision import datasets, transforms
from torch.utils.data import DataLoader, Subset,TensorDataset
from autoencoder import Autoencoder
import torchvision
from model2 import classification_model
import copy
import partition
from pca import PCADigitReducer
from autoencoder import reduce_dimensions
from training import train,test
from federated_learning import distribute_global_model, federated_averaging

# Initialization

In [2]:
# Predefined stuff

n_epochs = 3
batch_size_train = 64
batch_size_test = 1000
learning_rate = 0.01
momentum = 0.5
log_interval = 10
num_clusters = 2

random_seed = 1
torch.backends.cudnn.enabled = False
torch.manual_seed(random_seed)

In [3]:
# training and testing data as dataloaders

train_loader = torch.utils.data.DataLoader(
  torchvision.datasets.MNIST('/files/', train=True, download=True,
                             transform=torchvision.transforms.Compose([
                               torchvision.transforms.ToTensor(),
                               torchvision.transforms.Normalize(
                                 (0.1307,), (0.3081,))
                             ])),
  batch_size=batch_size_train, shuffle=True)

test_loader = torch.utils.data.DataLoader(
  torchvision.datasets.MNIST('/files/', train=False, download=True,
                             transform=torchvision.transforms.Compose([
                               torchvision.transforms.ToTensor(),
                               torchvision.transforms.Normalize(
                                 (0.1307,), (0.3081,))
                             ])),
  batch_size=batch_size_test, shuffle=True)

In [4]:
print((train_loader.dataset))

Dataset MNIST
    Number of datapoints: 60000
    Root location: /files/
    Split: Train
    StandardTransform
Transform: Compose(
               ToTensor()
               Normalize(mean=(0.1307,), std=(0.3081,))
           )


In [9]:
# get their respective data

train_loader_pca = copy.copy(train_loader)
test_loader_pca = copy.copy(test_loader)

train_loader_auto = copy.copy(train_loader)
test_loader_auto = copy.copy(test_loader)

In [11]:
# PCA DR, later encapsulate this shit
class CustomTensorDataset(TensorDataset):
    def __init__(self, *tensors):
        super().__init__(*tensors)
        self.data = tensors[0]
        self.targets = tensors[1] 


train_data = []
train_labels = []
for data, labels in train_loader_pca:
    train_data.append(data.view(data.size(0), -1))  
    train_labels.append(labels)
train_data = torch.cat(train_data, dim=0)  
train_labels = torch.cat(train_labels, dim=0)

train_data_np = train_data.numpy()

pca = PCADigitReducer(100)
train_data_reduced = pca.fit_transform(train_data_np)  

train_data_reconstructed_np = pca.inverse_transform(train_data_reduced) 
train_data_reconstructed = torch.tensor(train_data_reconstructed_np, dtype=torch.float32)

train_data_reconstructed = train_data_reconstructed.view(-1, 1, 28, 28)

train_data_reconstructed = (train_data_reconstructed - 0.1307) / 0.3081

batch_size_train = train_loader_pca.batch_size
train_dataset_pca = CustomTensorDataset(train_data_reconstructed, train_labels)
train_loader_reduced_pca = DataLoader(train_dataset_pca, batch_size=batch_size_train, shuffle=True)


In [12]:
trainingset_pca = train_loader_reduced_pca.dataset

print(trainingset_pca.targets)

tensor([4, 8, 8,  ..., 7, 0, 8])


In [13]:
# Autoencoder initialization, does take time because the Autoencoder has to be trained first. Later maybe store the parameters.
latent_dim = 100  
autoencoder = Autoencoder(latent_dim=latent_dim)
auto_criterion = nn.MSELoss()
auto_optimizer = optim.Adam(autoencoder.parameters(), lr=1e-3)
auto_num_epochs = 5
for epoch in range(auto_num_epochs): 
    for images, _ in train_loader_auto:
        auto_optimizer.zero_grad()
        reconstructed = autoencoder(images)
        loss = auto_criterion(reconstructed, images)  
        loss.backward()
        auto_optimizer.step()
        
    print(f"Epoch [{epoch+1}/5], Loss: {loss.item()}")


Epoch [1/5], Loss: 0.5411480665206909
Epoch [2/5], Loss: 0.5199205279350281
Epoch [3/5], Loss: 0.4910971224308014
Epoch [4/5], Loss: 0.519383430480957
Epoch [5/5], Loss: 0.5129168033599854


In [14]:
autoencoder.eval()
device = torch.device('cuda' if torch.cuda.is_available() else 'cpu')
latent_features, labels = reduce_dimensions(train_loader_auto, autoencoder.encoder, device)
latent_features = latent_features.detach()

reconstructed_images = autoencoder.decoder(latent_features.to(device))  
reconstructed_images = reconstructed_images.view(-1, 1, 28, 28)  # Reshape to [batch_size, channels, height, width]

reconstructed_dataset = CustomTensorDataset(reconstructed_images.cpu(), labels)  
reduced_train_loader_auto = DataLoader(reconstructed_dataset, batch_size=batch_size_train, shuffle=True)


In [15]:
# Now partition them into 4 clients for federated learning
# pca 4 clients
trainingset_pca = train_loader_reduced_pca.dataset
partitioned_data_pca = partition.balanced_dirichlet_partition(trainingset_pca, partitions_number=4, alpha=0.5)
# Check sizes

for i in partitioned_data_pca:
    print(len(partitioned_data_pca[i]))

13622
9683
19121
17574


In [18]:
# Apply clustering
import cluster
cluster = cluster.Cluster(num_clusters=num_clusters)

targets = trainingset_pca.targets
num_classes = len(set(targets)) 
clustered_data = cluster.apply_clustering(partitioned_data_pca, targets, num_classes)

partitioned_data_pca = clustered_data

for key, value in partitioned_data_pca.items():
    print(f"Key: {key}, Length of Values: {len(value)}")

Key: 0, Length of Values: 31196
Key: 1, Length of Values: 28804


In [19]:
pca_client_loaders = [
    DataLoader(Subset(trainingset_pca, indices), batch_size=batch_size_train, shuffle=True)
    for indices in partitioned_data_pca.values()
]

In [20]:
x = pca_client_loaders[0].dataset
for i in range(len(x)):
    sample, label = x[i]
    print(f"Sample {i} shape: {sample.shape}, Label: {label}")

Sample 0 shape: torch.Size([1, 28, 28]), Label: 6
Sample 1 shape: torch.Size([1, 28, 28]), Label: 4
Sample 2 shape: torch.Size([1, 28, 28]), Label: 0
Sample 3 shape: torch.Size([1, 28, 28]), Label: 3
Sample 4 shape: torch.Size([1, 28, 28]), Label: 2
Sample 5 shape: torch.Size([1, 28, 28]), Label: 5
Sample 6 shape: torch.Size([1, 28, 28]), Label: 5
Sample 7 shape: torch.Size([1, 28, 28]), Label: 6
Sample 8 shape: torch.Size([1, 28, 28]), Label: 3
Sample 9 shape: torch.Size([1, 28, 28]), Label: 0
Sample 10 shape: torch.Size([1, 28, 28]), Label: 0
Sample 11 shape: torch.Size([1, 28, 28]), Label: 8
Sample 12 shape: torch.Size([1, 28, 28]), Label: 9
Sample 13 shape: torch.Size([1, 28, 28]), Label: 0
Sample 14 shape: torch.Size([1, 28, 28]), Label: 0
Sample 15 shape: torch.Size([1, 28, 28]), Label: 0
Sample 16 shape: torch.Size([1, 28, 28]), Label: 7
Sample 17 shape: torch.Size([1, 28, 28]), Label: 9
Sample 18 shape: torch.Size([1, 28, 28]), Label: 0
Sample 19 shape: torch.Size([1, 28, 28]),

In [21]:
# autoencoder 4 clients
# classic
trainingset = train_loader.dataset
partitioned_data_classic = partition.balanced_dirichlet_partition(trainingset, partitions_number=4, alpha=0.5)

for i in partitioned_data_classic:
    print(len(partitioned_data_classic[i]))

13622
9683
19121
17574


In [22]:
# Apply clustering
import cluster
cluster = cluster.Cluster(num_clusters=num_clusters)

targets = trainingset.targets
num_classes = len(set(targets)) 
clustered_data = cluster.apply_clustering(partitioned_data_classic, targets, num_classes)

partitioned_data_classic = clustered_data

for key, value in partitioned_data_classic.items():
    print(f"Key: {key}, Length of Values: {len(value)}")

Key: 0, Length of Values: 31196
Key: 1, Length of Values: 28804


In [23]:
classic_client_loaders = [
    DataLoader(Subset(trainingset, indices), batch_size=batch_size_train, shuffle=True)
    for indices in partitioned_data_classic.values()
]

In [24]:
# auto 4 clients
trainingset_auto = reduced_train_loader_auto.dataset
print(trainingset_auto.targets)
print(trainingset_auto.data.shape)
partitioned_data_auto = partition.balanced_dirichlet_partition(trainingset_auto, partitions_number=4, alpha=0.5)
# Check sizes

for i in partitioned_data_auto:
    print(len(partitioned_data_auto[i]))
    #print(partitioned_data_auto[i])
#print(partitioned_data_auto)

tensor([2, 0, 9,  ..., 9, 6, 0])
torch.Size([60000, 1, 28, 28])
13622
9683
19121
17574


In [25]:
# Apply clustering
import cluster
cluster = cluster.Cluster(num_clusters=num_clusters)

targets = trainingset_auto.targets
num_classes = len(set(targets)) 
clustered_data = cluster.apply_clustering(partitioned_data_auto, targets, num_classes)

partitioned_data_auto = clustered_data

for key, value in partitioned_data_auto.items():
    print(f"Key: {key}, Length of Values: {len(value)}")

Key: 0, Length of Values: 31196
Key: 1, Length of Values: 28804


In [26]:
auto_client_loaders = [
    DataLoader(Subset(trainingset_auto, indices), batch_size=batch_size_train, shuffle=True)
    for indices in partitioned_data_auto.values()
]

In [27]:
# defining model for pca and autoencoder

global_model_pca = classification_model()
global_model_auto = classification_model()
gloabl_model_classic =classification_model()

num_clients = 2
# classic models
local_models_classic = [copy.deepcopy(global_model_pca) for _ in range(num_clients)]
# pca models 
local_models_pca = [copy.deepcopy(global_model_pca) for _ in range(num_clients)]
# autoencodere models
local_model_autoencoder = [copy.deepcopy(global_model_pca) for _ in range(num_clients)]

# Classic

In [28]:
rounds_classic = 4

for round_idx in range(rounds_classic):
    
    print(f"Round {round_idx + 1}/{rounds_classic}")

    local_weights_classic = []
    for client_idx, client_model in enumerate(local_models_classic):
        print(f"Training client {client_idx + 1}")
        
        optimizer = optim.SGD(client_model.parameters(), lr=learning_rate,
                      momentum=momentum)

        train_losses = []
        train_counter = []

        for epoch in range(1, n_epochs + 1):  
            train(epoch, client_model, classic_client_loaders[client_idx], optimizer, log_interval, train_losses, train_counter)
        
        client_weights = [param.data.numpy() for param in client_model.parameters()]
        local_weights_classic.append(client_weights)
        
    print(f"after training{local_models_classic}")
    global_weights_classic = federated_averaging(local_weights_classic)
    print(f"after fedaveraging{local_models_classic}")

    distribute_global_model(global_weights_classic,local_models_classic,single=False)

    distribute_global_model(global_weights_classic,gloabl_model_classic,single=True)
    test_losses = []
    test(gloabl_model_classic,test_loader,test_losses)


Round 1/4
Training client 1


C:\Users\nazek\Documents\Federated-Dimensionality-Reduction\model2.py:21: UserWarning: Implicit dimension choice for log_softmax has been deprecated. Change the call to include dim=X as an argument.
  return F.log_softmax(x)


Train Epoch: 1 [0/31196 (0%)]	Loss: 2.348960
Train Epoch: 1 [640/31196 (2%)]	Loss: 2.302440
Train Epoch: 1 [1280/31196 (4%)]	Loss: 2.282365
Train Epoch: 1 [1920/31196 (6%)]	Loss: 2.269988
Train Epoch: 1 [2560/31196 (8%)]	Loss: 2.187158
Train Epoch: 1 [3200/31196 (10%)]	Loss: 2.202795
Train Epoch: 1 [3840/31196 (12%)]	Loss: 2.056279
Train Epoch: 1 [4480/31196 (14%)]	Loss: 2.200701
Train Epoch: 1 [5120/31196 (16%)]	Loss: 1.994727
Train Epoch: 1 [5760/31196 (18%)]	Loss: 1.891420
Train Epoch: 1 [6400/31196 (20%)]	Loss: 1.798109
Train Epoch: 1 [7040/31196 (23%)]	Loss: 1.631679
Train Epoch: 1 [7680/31196 (25%)]	Loss: 1.571886
Train Epoch: 1 [8320/31196 (27%)]	Loss: 1.560301
Train Epoch: 1 [8960/31196 (29%)]	Loss: 1.412520
Train Epoch: 1 [9600/31196 (31%)]	Loss: 1.076035
Train Epoch: 1 [10240/31196 (33%)]	Loss: 1.411802
Train Epoch: 1 [10880/31196 (35%)]	Loss: 1.421042
Train Epoch: 1 [11520/31196 (37%)]	Loss: 1.293575
Train Epoch: 1 [12160/31196 (39%)]	Loss: 1.244142
Train Epoch: 1 [12800/311

C:\Users\nazek\anaconda3\Lib\site-packages\torch\nn\_reduction.py:51: UserWarning: size_average and reduce args will be deprecated, please use reduction='sum' instead.
  warnings.warn(warning.format(ret))



Test set: Avg. loss: 0.2129, Accuracy: 9485/10000 (95%)

Round 2/4
Training client 1
Train Epoch: 1 [0/31196 (0%)]	Loss: 0.321416
Train Epoch: 1 [640/31196 (2%)]	Loss: 0.476170
Train Epoch: 1 [1280/31196 (4%)]	Loss: 0.294536
Train Epoch: 1 [1920/31196 (6%)]	Loss: 0.404360
Train Epoch: 1 [2560/31196 (8%)]	Loss: 0.363982
Train Epoch: 1 [3200/31196 (10%)]	Loss: 0.427913
Train Epoch: 1 [3840/31196 (12%)]	Loss: 0.317330
Train Epoch: 1 [4480/31196 (14%)]	Loss: 0.473714
Train Epoch: 1 [5120/31196 (16%)]	Loss: 0.483788
Train Epoch: 1 [5760/31196 (18%)]	Loss: 0.393559
Train Epoch: 1 [6400/31196 (20%)]	Loss: 0.594818
Train Epoch: 1 [7040/31196 (23%)]	Loss: 0.366056
Train Epoch: 1 [7680/31196 (25%)]	Loss: 0.512064
Train Epoch: 1 [8320/31196 (27%)]	Loss: 0.381132
Train Epoch: 1 [8960/31196 (29%)]	Loss: 0.364921
Train Epoch: 1 [9600/31196 (31%)]	Loss: 0.444743
Train Epoch: 1 [10240/31196 (33%)]	Loss: 0.515504
Train Epoch: 1 [10880/31196 (35%)]	Loss: 0.466725
Train Epoch: 1 [11520/31196 (37%)]	Loss

# PCA

In [29]:


rounds_pca = 4

for round_idx in range(rounds_pca):
    
    print(f"Round {round_idx + 1}/{rounds_pca}")

    local_weights_pca = []
    for client_idx, client_model in enumerate(local_models_pca):
        print(f"Training client {client_idx + 1}")
        
        optimizer = optim.SGD(client_model.parameters(), lr=learning_rate,
                      momentum=momentum)

        train_losses = []
        train_counter = []


        for epoch in range(1, n_epochs + 1):  
            train(epoch, client_model, pca_client_loaders[client_idx], optimizer, log_interval, train_losses, train_counter)
        
        client_weights = [param.data.numpy() for param in client_model.parameters()]
        local_weights_pca.append(client_weights)
        
    print(f"after training{local_models_pca}")
    global_weights_pca = federated_averaging(local_weights_pca)
    print(f"after fedaveraging{local_models_pca}")

    distribute_global_model(global_weights_pca,local_models_pca,single=False)

    distribute_global_model(global_weights_pca,global_model_pca,single=True)
    test_losses = []
    test(global_model_pca,test_loader_pca,test_losses)


    


Round 1/4
Training client 1
Train Epoch: 1 [0/31196 (0%)]	Loss: 2.509796
Train Epoch: 1 [640/31196 (2%)]	Loss: 2.279862
Train Epoch: 1 [1280/31196 (4%)]	Loss: 2.213033
Train Epoch: 1 [1920/31196 (6%)]	Loss: 2.011986
Train Epoch: 1 [2560/31196 (8%)]	Loss: 1.786623
Train Epoch: 1 [3200/31196 (10%)]	Loss: 1.723328
Train Epoch: 1 [3840/31196 (12%)]	Loss: 1.703966
Train Epoch: 1 [4480/31196 (14%)]	Loss: 1.542185
Train Epoch: 1 [5120/31196 (16%)]	Loss: 1.444312
Train Epoch: 1 [5760/31196 (18%)]	Loss: 1.119421
Train Epoch: 1 [6400/31196 (20%)]	Loss: 1.404192
Train Epoch: 1 [7040/31196 (23%)]	Loss: 1.025935
Train Epoch: 1 [7680/31196 (25%)]	Loss: 0.997201
Train Epoch: 1 [8320/31196 (27%)]	Loss: 1.172788
Train Epoch: 1 [8960/31196 (29%)]	Loss: 1.057783
Train Epoch: 1 [9600/31196 (31%)]	Loss: 1.032138
Train Epoch: 1 [10240/31196 (33%)]	Loss: 1.027708
Train Epoch: 1 [10880/31196 (35%)]	Loss: 0.951624
Train Epoch: 1 [11520/31196 (37%)]	Loss: 1.101363
Train Epoch: 1 [12160/31196 (39%)]	Loss: 0.8039

In [30]:
data_test = auto_client_loaders[0].dataset
for i in range(len(data_test)):
    sample, label = data_test[i]
    print(f"Sample {i} shape: {sample.shape}, Label: {label}")

Sample 0 shape: torch.Size([1, 28, 28]), Label: 6
Sample 1 shape: torch.Size([1, 28, 28]), Label: 4
Sample 2 shape: torch.Size([1, 28, 28]), Label: 0
Sample 3 shape: torch.Size([1, 28, 28]), Label: 3
Sample 4 shape: torch.Size([1, 28, 28]), Label: 2
Sample 5 shape: torch.Size([1, 28, 28]), Label: 5
Sample 6 shape: torch.Size([1, 28, 28]), Label: 5
Sample 7 shape: torch.Size([1, 28, 28]), Label: 6
Sample 8 shape: torch.Size([1, 28, 28]), Label: 3
Sample 9 shape: torch.Size([1, 28, 28]), Label: 0
Sample 10 shape: torch.Size([1, 28, 28]), Label: 0
Sample 11 shape: torch.Size([1, 28, 28]), Label: 8
Sample 12 shape: torch.Size([1, 28, 28]), Label: 9
Sample 13 shape: torch.Size([1, 28, 28]), Label: 0
Sample 14 shape: torch.Size([1, 28, 28]), Label: 0
Sample 15 shape: torch.Size([1, 28, 28]), Label: 0
Sample 16 shape: torch.Size([1, 28, 28]), Label: 7
Sample 17 shape: torch.Size([1, 28, 28]), Label: 9
Sample 18 shape: torch.Size([1, 28, 28]), Label: 0
Sample 19 shape: torch.Size([1, 28, 28]),

# Autoencoder

In [31]:
print(len(auto_client_loaders[0].dataset))


31196


In [32]:
rounds_auto = 4

for round_idx in range(rounds_auto):
    print(f"Round {round_idx + 1}/{rounds_auto}")

    local_weights_auto = []
    for client_idx, client_model in enumerate(local_model_autoencoder):
        print(f"Training client {client_idx + 1}")
        
        optimizer = optim.SGD(client_model.parameters(), lr=learning_rate,
                      momentum=momentum)
        
        train_losses = []
        train_counter = []

        for epoch in range(1, n_epochs + 1):  
            train(epoch, client_model, auto_client_loaders[client_idx], optimizer, log_interval, train_losses, train_counter)
        
        client_weights = [param.data.numpy() for param in client_model.parameters()]
        local_weights_auto.append(client_weights)
        
    global_weights_auto = federated_averaging(local_weights_auto)

    distribute_global_model(global_weights_auto,local_model_autoencoder,single=False)

    distribute_global_model(global_weights_auto, global_model_auto,single=True)
    test_losses = []
    test(global_model_auto,test_loader_auto,test_losses)

Round 1/4
Training client 1
Train Epoch: 1 [0/31196 (0%)]	Loss: 2.312782
Train Epoch: 1 [640/31196 (2%)]	Loss: 2.323983
Train Epoch: 1 [1280/31196 (4%)]	Loss: 2.287097
Train Epoch: 1 [1920/31196 (6%)]	Loss: 2.299899
Train Epoch: 1 [2560/31196 (8%)]	Loss: 2.277451
Train Epoch: 1 [3200/31196 (10%)]	Loss: 2.280685
Train Epoch: 1 [3840/31196 (12%)]	Loss: 2.253656
Train Epoch: 1 [4480/31196 (14%)]	Loss: 2.282039
Train Epoch: 1 [5120/31196 (16%)]	Loss: 2.235473
Train Epoch: 1 [5760/31196 (18%)]	Loss: 2.227440
Train Epoch: 1 [6400/31196 (20%)]	Loss: 2.233433
Train Epoch: 1 [7040/31196 (23%)]	Loss: 2.198077
Train Epoch: 1 [7680/31196 (25%)]	Loss: 2.235718
Train Epoch: 1 [8320/31196 (27%)]	Loss: 2.192060
Train Epoch: 1 [8960/31196 (29%)]	Loss: 2.115482
Train Epoch: 1 [9600/31196 (31%)]	Loss: 2.082237
Train Epoch: 1 [10240/31196 (33%)]	Loss: 2.118844
Train Epoch: 1 [10880/31196 (35%)]	Loss: 2.055287
Train Epoch: 1 [11520/31196 (37%)]	Loss: 1.981347
Train Epoch: 1 [12160/31196 (39%)]	Loss: 1.9113